# Relative Strength Index

The common indicator to detect over-bought or over-sold situation.

## Comment
This indicator looks like random signal. When base portfollio weight on RSI, the result is close to passive rebalance to the mean weight. 

## Data

In [1]:
from btbox import *
from pandas import Series

In [2]:
SYMBOL = 'SPY'
START = '2000-01-01'
WINDOW = 21
INTERVAL = 252

In [3]:
dfs = {SYMBOL: import_yahoo_csv(f'../../_data_/{SYMBOL}_bar1day.csv')}

## Benchmark

In [4]:
class BM_AllInAndForget(Strategy):

    def initial(self, b: Broker):
        b.portfolio.trade_target_weight(SYMBOL, 1)

class BM_KeepAtHalf(Strategy):

    @interval(INTERVAL)
    def step(self, b: Broker):
        b.portfolio.trade_target_weight(SYMBOL, 0.5)

## Indicator

In [5]:
def rsi_follow(period: int, win: Series, factor: int) -> float:
    delta = win.diff().dropna()
    up = delta.clip(lower=0)
    dn = abs(delta.clip(upper=0))
    ma_up = up.iloc[-period:].mean()
    ma_dn = dn.iloc[-period:].mean()
    rs = ma_up / ma_dn
    rsi = 100 - (100 / (1 + rs))
    p_weight = rsi / 100 * factor
    assert isinstance(p_weight, float)
    return p_weight

## Strategy

In [6]:
def ST_rsi_follow(period: int, factor: float):

    class ST(Strategy):
        name = f'ST_rsi({period})_follow({factor})'

        @interval(21)
        def step(self, b: Broker):
            win = b.market.get_close_window(SYMBOL)
            weight = rsi_follow(period, win, factor)
            b.portfolio.trade_target_weight(SYMBOL, weight)
            self.journal.mark(weight, 'target-weight')

    return ST

## Backtest

In [7]:
bt = create_backtest(
    [
        BM_AllInAndForget,
        BM_KeepAtHalf,
        ST_rsi_follow(14, 1.0),
        ST_rsi_follow(14, 2.0),
    ],
    dfs,
    start=START,
    window=WINDOW,
)

In [8]:
results = bt.run()

## Dashboard

In [9]:
results.dashboard_pretty()

## Equity Curve

In [10]:
results.plot(log_y=True)

In [11]:
results['ST_rsi(14)_follow(1.0)'].journals['target-weight'].ffill.plot_line_under_price(SYMBOL)